In [1]:
import trimesh
import pyrender
import open3d as o3d
import os
import numpy as np

import plotly.express as px
import plotly.graph_objects as go

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
def plane_estimation(points, colors, distance_threshold=0.01, ransac_n=3, num_iterations=1000, verbose=True):
        pcd = o3d.geometry.PointCloud()
        pcd.points = o3d.utility.Vector3dVector(points)
        pcd.colors = o3d.utility.Vector3dVector(colors)
        plane_model, inliers = pcd.segment_plane(distance_threshold=distance_threshold, ransac_n=ransac_n, num_iterations=num_iterations)
        [a, b, c, d] = plane_model
        if verbose:
            print("Plane equation: {:.2f}x + {:.2f}y + {:.2f}z + {:.2f} = 0".format(a, b, c, d))
            print("Number of inliers: {}".format(len(inliers)))
        inlier_cloud = pcd.select_by_index(inliers)
        outlier_cloud = pcd.select_by_index(inliers, invert=True)
        return {
            "plane_model": plane_model,
            "inliers": inliers,
            "inlier_cloud": inlier_cloud,
            "outlier_cloud": outlier_cloud
        }

In [3]:
def preprocess(pcd, use_rgb=True, max_points=40000):
        num_points = np.asarray(pcd.points).shape[0]

        if num_points < max_points:
            num_pad_points = max_points - num_points

            if num_pad_points > 0:
                # Randomly select points from the original point cloud for padding
                pad_indices = np.random.randint(0, num_points, size=(num_pad_points,))
                pad_points = np.asarray(pcd.points)[pad_indices]
                if use_rgb:
                    pad_colors = np.asarray(pcd.colors)[pad_indices]
                new_pcd = o3d.geometry.PointCloud()
                new_pcd.points = o3d.utility.Vector3dVector(pad_points)
                if use_rgb:
                    new_pcd.colors = o3d.utility.Vector3dVector(pad_colors)
                pcd += new_pcd
        else:
            pcd = pcd.random_down_sample(max_points / num_points)
            # In case downsampling results in fewer points
            if np.asarray(pcd.points).shape[0] < max_points:
                pcd = preprocess(pcd, use_rgb=use_rgb, max_points=max_points)
        return pcd

In [4]:
def estimate_rotation(plane_model, z_up=True):
    # Normal vector of the plane
    a, b, c, d = plane_model
    n = np.array([a, b, c])

    # Z-axis unit vector
    if z_up:
        k = np.array([0, 0, 1])
    else:
        # z down case
        k = np.array([0, 0, -1])

    # Calculate the rotation axis (cross product of n and k)
    axis = np.cross(n, k)

    # Normalize the rotation axis
    axis_normalized = axis / np.linalg.norm(axis)

    # Calculate the angle of rotation (dot product and arccosine)
    cos_theta = np.dot(n, k) / np.linalg.norm(n)
    theta = np.arccos(cos_theta)
    # theta = 2.1
    print(theta)

    # Rodrigues' rotation formula
    # Skew-symmetric matrix of axis
    axis_skew = np.array([[0, -axis_normalized[2], axis_normalized[1]],
                        [axis_normalized[2], 0, -axis_normalized[0]],
                        [-axis_normalized[1], axis_normalized[0], 0]])

    # Rotation matrix
    R = np.eye(3) + np.sin(theta) * axis_skew + (1 - np.cos(theta)) * np.dot(axis_skew, axis_skew)
    T = np.eye(4)
    T[:3, :3] = R
    return T

In [5]:
def plotly_draw_3d_pcd(pcd_points, pcd_colors=None, addition_points=None, marker_size=3, equal_axis=True, title="", offline=False, no_background=False, default_rgb_str="(255,0,0)",additional_point_draw_lines=False, uniform_color=False):

    if pcd_colors is None:
        color_str = [f'rgb{default_rgb_str}' for _ in range(pcd_points.shape[0])]
    else:
        color_str = ['rgb('+str(r)+','+str(g)+','+str(b)+')' for r,g,b in pcd_colors]

    # Extract x, y, and z columns from the point cloud
    x_vals = pcd_points[:, 0]
    y_vals = pcd_points[:, 1]
    z_vals = pcd_points[:, 2]

    # Create the scatter3d plot
    rgbd_scatter = go.Scatter3d(
        x=x_vals,
        y=y_vals,
        z=z_vals,
        mode='markers',
        marker=dict(size=3, color=color_str, opacity=0.8)
    )
    data = [rgbd_scatter]
    if addition_points is not None:
        # print(addition_points.shape)
        assert(addition_points[0].shape[-1] == 3)
        # # check if addition_points are three dimensional
        if type(addition_points) == np.ndarray:
            if len(addition_points.shape) == 2:
                addition_points = [addition_points]
        for points in addition_points:
            x = points[:, 0]
            y = points[:, 1]
            z = points[:, 2]
            if additional_point_draw_lines:
                mode = "lines+markers"
            else:
                mode = "markers"
            marker_dict = dict(size=marker_size,
                                opacity=0.8)
            
            if uniform_color:
                marker_dict["color"] = f'rgb{default_rgb_str}'
            rgbd_scatter2 = go.Scatter3d(
                x=x,
                y=y,
                z=z,
                mode=mode,
                marker=marker_dict,
                )
            data.append(rgbd_scatter2)

    if equal_axis:
        scene_dict = dict(   
            aspectmode='data',  
        )
    else:
        scene_dict = dict()
    # Set the layout for the plot
    layout = go.Layout(
        margin=dict(l=0, r=0, b=0, t=0),
        # axes range
        scene=scene_dict,
        title=dict(text=title, automargin=True)
    )

    fig = go.Figure(data=data, layout=layout)

    if no_background:
        fig.update_layout(
        scene=dict(
            xaxis=dict(showbackground=False, zeroline=False, showgrid=False, showticklabels=False, showaxeslabels=False, visible=False),
            yaxis=dict(showbackground=False, zeroline=False, showgrid=False, showticklabels=False, showaxeslabels=False, visible=False),
            zaxis=dict(showbackground=False, zeroline=False, showgrid=False, showticklabels=False, showaxeslabels=False, visible=False),
        ),
        paper_bgcolor='rgba(0,0,0,0)',  # Transparent background
        plot_bgcolor='rgba(0,0,0,0)',  # Transparent background
        margin=dict(l=0, r=0, b=0, t=0),  # No margins
        showlegend=False,
    )


    if not offline:
        fig.show()
    else:
        return fig


In [6]:
in_folder = "./pcds_and_meshes/"

mesh = o3d.io.read_triangle_mesh(os.path.join(in_folder, "mesh.glb"))

pts3d = np.load(os.path.join(in_folder, "pts3d.npy"))
colors = np.load(os.path.join(in_folder, "colors.npy"))

In [7]:
viewer = o3d.visualization.Visualizer()
viewer.create_window()

viewer.add_geometry(mesh)
opt = viewer.get_render_option()
opt.show_coordinate_frame = True
opt.background_color = np.asarray([0.5, 0.5, 0.5])
viewer.run()
viewer.destroy_window()

#o3d.visualization.draw_geometries([mesh])

In [50]:
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(pts3d)
pcd.colors = o3d.utility.Vector3dVector(colors)

pcd = preprocess(pcd, use_rgb=True, max_points=40000)

fig = plotly_draw_3d_pcd(np.asarray(pcd.points), np.asarray(pcd.colors), title="Original Point Cloud", offline=True)
display(fig)